<a href="https://colab.research.google.com/github/google-research/protein-ligand-binding-free-energy-calculations/blob/matteo-dev/colab_tutorial/intro_gromacs_tutorial.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

##### Copyright 2022 Google LLC.

In [ ]:
#@title Licensed under the Apache License, Version 2.0 (the "License");
# you may not use this file except in compliance with the License.
# You may obtain a copy of the License at
#
# https://www.apache.org/licenses/LICENSE-2.0
#
# Unless required by applicable law or agreed to in writing, software
# distributed under the License is distributed on an "AS IS" BASIS,
# WITHOUT WARRANTIES OR CONDITIONS OF ANY KIND, either express or implied.
# See the License for the specific language governing permissions and
# limitations under the License.

# Brief Gromacs+Colab Tutorial

## Note

1. If you use a public colab instance, remember to change your runtime type to GPU
2. If you deployed a custom GCE runtime, please connect to a GPU VM instance.

## Summary

1. Pull Gromacs 2022.3 binary compiled specifically for Colab GPU environment and install the software.
2. Install Gromacs Python API on the fly, together with other packages used in the tutorial.
3. Run simulations for benchmarks and show how to use the official GMX
Python API to modify inputs.
4. Visualize the output conformation for the longer simulation.

In [ ]:
#@title Install Gromacs and Gromacs Python API
!wget https://storage.googleapis.com/gromacs-bin/gromacs-avx2_256-cuda-11_2.tar.gz -O /tmp/gromacs.tar.gz
!wget https://storage.googleapis.com/gromacs-bin/benchMEM.tpr -O /tmp/benchMEM.tpr
!wget https://storage.googleapis.com/gromacs-bin/hif2a_eq.tpr -O /tmp/hif2a_eq.tpr

!tar zxf /tmp/gromacs.tar.gz
!sudo rm -rf /usr/local/gromacs
!sudo mv gromacs-avx /usr/local/gromacs
!rm /tmp/gromacs.tar.gz

!pip3 install --upgrade pip
!pip3 install setuptools wheel cmake pybind11 py3DMol
!gmxapi_ROOT=/usr/local/gromacs/ pip3 install --no-cache-dir gmxapi

--2022-11-12 01:12:53--  https://storage.googleapis.com/gromacs-bin/gromacs-avx2_256-cuda-11_2.tar.gz
Resolving storage.googleapis.com (storage.googleapis.com)... 74.125.199.128, 74.125.20.128, 74.125.142.128, ...
Connecting to storage.googleapis.com (storage.googleapis.com)|74.125.199.128|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 23920923 (23M) [application/x-gzip]
Saving to: ‘/tmp/gromacs.tar.gz’

/tmp/gromacs.tar.gz 100%[===================>]  22.81M  85.3MB/s    in 0.3s    

2022-11-12 01:12:53 (85.3 MB/s) - ‘/tmp/gromacs.tar.gz’ saved [23920923/23920923]

--2022-11-12 01:12:53--  https://storage.googleapis.com/gromacs-bin/benchMEM.tpr
Resolving storage.googleapis.com (storage.googleapis.com)... 74.125.199.128, 74.125.20.128, 74.125.142.128, ...
Connecting to storage.googleapis.com (storage.googleapis.com)|74.125.199.128|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 3461380 (3.3M) [application/octet-stream]
Saving to: ‘/tm

In [ ]:
#@title Set Level for Logging
#@markdown Sets the python logging level. This is useful for debugging.
import logging

log_level = 'INFO' #@param ['DEBUG', 'INFO', 'ERROR']

_log_level = {
    'DEBUG': logging.DEBUG,
    'INFO': logging.INFO,
    'ERROR': logging.ERROR
}

logging.basicConfig(level=_log_level[log_level])

In [ ]:
#@title [Please Rerun after Restart] Create a Session
#@markdown Please rerun this cell every time when you restart the runtime.
#@markdown A new session ID will be created for a new colab runtime session.
#@markdown Run this cell again will refresh the session ID.

import os
import time
import gmxapi


# Sets a session ID for this session.
_SESSION_ID = str(int(time.time())) #@param

# Monkey patch this session ID into the gmxapi.operation.ResourceManager.
# Hack. Do not use in the user code.
# This is temporarily added to allow users to start from a new set of working
# directories for all the mdrun launches. GMX API doesn't expose the
# underlying resource manager or context yet.
def operation_id(self):
  return f"{self._base_operation_id}_{_SESSION_ID}"
gmxapi.operation.ResourceManager.operation_id = property(operation_id)


def get_work_dir(md_output):
  values = [v for v in md_output.values()]
  return values[0].result()


def tail_log(md_output, output_file_base, last_n_lines=6):
  work_dir = get_work_dir(md_output)

  with open(os.path.join(work_dir, output_file_base + '.log'), 'r') as log:
    for line in log.readlines()[-last_n_lines:]:
      print(line)

print("Session ID: ", _SESSION_ID)

INFO:gmxapi:Importing gmxapi.
INFO:gmxapi.operation:Importing gmxapi.operation
INFO:gmxapi.commandline:Importing gmxapi.commandline
INFO:gmxapi.simulation.workflow:Importing gmx.workflow
INFO:gmxapi.simulation.workflow:Using schema version gmxapi_workspec_0_1.
INFO:gmxapi.mdrun:Importing gmxapi.simulation.mdrun
INFO:gmxapi.read_tpr:Importing gmxapi.simulation.read_tpr
INFO:gmxapi.modify_input:Importing gmxapi.simulation.modify_input


Session ID:  1668215607


In [ ]:
#@title Run a Short Simulation for Benchmark

# Read a TPR sample and run it.
# The TPR file configures a 20ps simulation.
input_tpr = gmxapi.read_tpr('/tmp/benchMEM.tpr')

# Can specify computations to GPU.
output_file_base = 'short'
md = gmxapi.mdrun(input_tpr, runtime_args={
    '-nb': 'gpu', '-pme': 'gpu', '-pmefft': 'gpu', '-bonded': 'gpu',
    '-deffnm': output_file_base})

# Run the simulation
md.run()

# Tail performance
tail_log(md.output, output_file_base)

               Core t (s)   Wall t (s)        (%)

       Time:      132.912       66.457      200.0

                 (ns/day)    (hour/ns)

Performance:       26.005        0.923

Finished mdrun on rank 0 Wed Nov  9 16:09:26 2022





In [ ]:
#@title Modified Params and Run A Longer Simulation
# Run the simulation for 40 ps.
output_file_base = 'long2'

modified_tpr = gmxapi.modify_input(
    input=input_tpr, parameters={'nsteps': 20000, 'nstlist': 100})

md = gmxapi.mdrun(modified_tpr, runtime_args={
    '-nb': 'gpu', '-pme': 'gpu', '-pmefft': 'gpu', '-bonded': 'gpu',
    '-deffnm': output_file_base})
md.run()

# Tail performance
tail_log(md.output, output_file_base)

               Core t (s)   Wall t (s)        (%)

       Time:      217.043      108.522      200.0

                 (ns/day)    (hour/ns)

Performance:       31.848        0.754

Finished mdrun on rank 0 Wed Nov  9 16:11:16 2022





In [ ]:
#@title What about a binding affinity simulation with HIF2a?
output_file_base = 'hif'

input_tpr = gmxapi.read_tpr('/tmp/hif2a_eq.tpr')
modified_tpr = gmxapi.modify_input(
    input=input_tpr, parameters={'nsteps': 20000, 'nstlist': 100})
md = gmxapi.mdrun(modified_tpr, runtime_args={
    '-nb': 'gpu', '-pme': 'gpu', '-pmefft': 'gpu', '-bonded': 'gpu',
    '-deffnm': output_file_base})
md.run()

# Tail performance
tail_log(md.output, output_file_base)

               Core t (s)   Wall t (s)        (%)

       Time:      199.208       99.604      200.0

                 (ns/day)    (hour/ns)

Performance:       34.699        0.692

Finished mdrun on rank 0 Wed Nov  9 16:14:36 2022





## Visualization

Visualize the output from the above HIF2A simulation.
We use py3DMol to visualize the output gro file.

In [ ]:
#@title Visualize the output conformation of the HIF2A simulation.
import py3Dmol

view = py3Dmol.view()
work_dir = get_work_dir(md.output)

view.addModel(
    open(os.path.join(work_dir, output_file_base + '.gro'), 'r').read(), 'gro')

view.zoomTo()
view.setBackgroundColor('white')
view.setStyle({}, {'cartoon': {'color': 'spectrum'}})

view.show()

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol